# &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Background

The training dataset contains demographic information and what financial services are used by approximately 10,000 individuals across Tanzania. This data was extracted from the FSDT Finscope 2017 survey and prepared specifically for this challenge.

Each individual is classified into four mutually exclusive categories:

No_financial_services: Individuals who do not use mobile money, do not save, do not have credit, and do not have insurance
Other_only: Individuals who do not use mobile money, but do use at least one of the other financial services (savings, credit, insurance)
Mm_only: Individuals who use mobile money only
Mm_plus: Individuals who use mobile money and also use at least one of the other financial services (savings, credit, insurance)

This dataset is the geospatial mapping of all cash outlets in Tanzania in 2012. Cash outlets in this case included commercial banks, community banks, ATMs, microfinance institutions, mobile money agents, bus stations and post offices. This data was collected by FSDT.

# &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Instructions

**1. Examine the dataset. Are there any missing observations or columns where the data do not seem valid?**

In [1]:
# Importing Libraries
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt
import numpy as np
from plotly import __version__
import cufflinks as cf
from plotly.offline import download_plotlyjs,init_notebook_mode,plot,iplot
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import folium
from folium.plugins import MarkerCluster

init_notebook_mode(connected=True)
cf.go_offline()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Examining the dataset

In [2]:
# Getting the data
data = pd.read_csv("Data/training.csv")

# Minimum info about the data
rows, columns = data.shape
print("Total columns:\t{}\nTotal rows:\t{}".format(columns, rows))

# A view of the first five rows
data.head()

Total columns:	37
Total rows:	7094


ID  Q1  Q2  Q3  Q4  Q5  Q6  Q7  Q8_1  Q8_2  ...  Q17  Q18  Q19  Latitude  \
0  5086  98   2   3   1   1   2   2     0     0  ...   -1    4    4 -4.460442   
1  1258  40   1   1   3   5   1   1     1     0  ...    4    1    4 -6.176438   
2   331  18   2   4   6   3   2   1     0     0  ...   -1    1    1 -6.825702   
3  6729  50   1   1   3   1   1   1     0     0  ...   -1    1    4 -3.372049   
4  8671  34   1   1   1   1   2   1     0     1  ...   -1    1    4 -7.179645   

   Longitude  mobile_money  savings  borrowing  insurance  \
0  29.811396             0        0          0          0   
1  39.244871             1        1          1          0   
2  37.652798             1        0          0          0   
3  35.808307             1        0          1          0   
4  31.039095             1        1          0          1   

   mobile_money_classification  
0                            0  
1                            3  
2                            2  
3                            3  
4                            3  

[5 rows x 37 columns]

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;A look at missing values

In [3]:
# Missing data
print("Number of columns with missing values: {}".format(len(data.columns[data.isnull().any()])))

Number of columns with missing values: 0


**2. Get basic descriptive statistics for the dataset.**

First things first: A bit of data cleaning

In [4]:
# Renaming Columns 
columns_names = {"Q1":"age", "Q2": "gender", "Q3":"marital_status",
                 "Q4":"education", "Q5":"residents", "Q6": "land_ownership",
                 "Q7": "mobile_phone_ownership", "Q8_1": "salaries_or_Wages",
                 "Q8_2": "trading", "Q8_3": "services", "Q8_4": "piece_work",
                 "Q8_5": "rental_income", "Q8_6": "interest", "Q8_7": "pension",
                 "Q8_8": "welfare", "Q8_9": "rely_on_someone", "Q8_10": "dependent",
                 "Q8_11": "other", "Q9": "employeer", "Q10": "trading_goods", 
                 "Q11": "type_of_Service", "Q12":"sent_money", "Q13": "transfer_money",
                 "Q14": "received_money", "Q15": "received_money_days", "Q16":"usage_goods_services", "Q17":"usage_bills",
                 "Q18": "literacy_in_kiswhahili", "Q19": "literacy_in_english"}

data = data.rename(columns_names, axis=1)

# Adding categorical variables
gender_names = {1: "Male", 2: "Female"}
data["Gender"] = data["gender"].map(gender_names)

marital_names ={1: "Married", 2: "Divorced", 3: "Widowed", 4: "Single/Never Married"}
data["Marital Status"] = data["marital_status"].map(marital_names)

education_names = {1: "No Formal Education", 2: "Some Primary", 3: "Primary Completed", 4: "Post Primary", 5: "Some Secondary", 6: "University", 7: "Don't Know"}
data["Education"] = data["education"].map(education_names)

land_ownership_names = {1: "Yes", 2: "No"}
data["Land Ownership"] = data["land_ownership"].map(land_ownership_names)

usage_goods_services_names = {-1: "not applicable", 1: "Never", 2: "Daily", 3: "Weekly", 4: "Monthly", 5: "Less often than monthly"}
data["Usage Goods Service"] = data["usage_goods_services"].map(usage_goods_services_names)

usage_bills_names = {-1: "not applicable", 1: "Never", 2: "Daily", 3: "Weekly", 4: "Monthly", 5: "Less often than monthly"}
data["Usage Bills"] = data["usage_bills"].map(usage_bills_names)

mobile_money_classification_names = {0: "No Mobile Money and no other Financial Service", 1: "No Mobile Money, one other financial service", 2: "Mobile Money Only", 3: "Mobile Money plus"}
data["Mobile Money Classification"] = data["mobile_money_classification"].map(mobile_money_classification_names)

##### Basic descriptive statistics of numerical variables

In [5]:
data.describe()

ID          age       gender  marital_status    education  \
count  7094.000000  7094.000000  7094.000000     7094.000000  7094.000000   
mean   4742.627291    38.239498     1.559910        1.787426     3.060051   
std    2731.120086    16.332148     0.496433        1.165160     1.557779   
min       1.000000    16.000000     1.000000        1.000000     1.000000   
25%    2397.250000    25.000000     1.000000        1.000000     2.000000   
50%    4744.500000    35.000000     2.000000        1.000000     3.000000   
75%    7105.000000    48.000000     2.000000        3.000000     3.000000   
max    9459.000000   100.000000     2.000000        4.000000     8.000000   

         residents  land_ownership  mobile_phone_ownership  salaries_or_Wages  \
count  7094.000000     7094.000000             7094.000000        7094.000000   
mean      2.548915        1.840569                1.397942           0.062165   
std       1.534257        0.366103                0.489508           0.241472   
min       1.000000        1.000000                1.000000           0.000000   
25%       1.000000        2.000000                1.000000           0.000000   
50%       3.000000        2.000000                1.000000           0.000000   
75%       4.000000        2.000000                2.000000           0.000000   
max       6.000000        2.000000                2.000000           1.000000   

           trading  ...  usage_bills  literacy_in_kiswhahili  \
count  7094.000000  ...  7094.000000             7094.000000   
mean      0.630110  ...    -0.431914                1.860164   
std       0.482809  ...     1.489879                1.351372   
min       0.000000  ...    -1.000000                1.000000   
25%       0.000000  ...    -1.000000                1.000000   
50%       1.000000  ...    -1.000000                1.000000   
75%       1.000000  ...    -1.000000                4.000000   
max       1.000000  ...     5.000000                5.000000   

       literacy_in_english     Latitude    Longitude  mobile_money  \
count          7094.000000  7094.000000  7094.000000   7094.000000   
mean              3.163378    -6.034378    35.354029      0.553989   
std               1.317691     2.720888     2.899511      0.497112   
min               1.000000   -11.467463    29.639578      0.000000   
25%               2.000000    -8.275387    32.935429      0.000000   
50%               4.000000    -6.087854    35.073326      1.000000   
75%               4.000000    -3.517053    38.351815      1.000000   
max               5.000000    -1.084000    40.258744      1.000000   

           savings    borrowing    insurance  mobile_money_classification  
count  7094.000000  7094.000000  7094.000000                  7094.000000  
mean      0.461517     0.432901     0.151255                     1.799267  
std       0.498552     0.495512     0.358322                     1.196955  
min       0.000000     0.000000     0.000000                     0.000000  
25%       0.000000     0.000000     0.000000                     1.000000  
50%       0.000000     0.000000     0.000000                     2.000000  
75%       1.000000     1.000000     0.000000                     3.000000  
max       1.000000     1.000000     1.000000                     3.000000  

[8 rows x 37 columns]

**3. Create appropriate graphs to visually represent the relationship between financial services accessed (non-mobile, mobile, both) and age, gender, marital status, land ownership and type of income.**

### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;An overview of the Mobile Money Market Segments

In [6]:
(pd.DataFrame(data["Mobile Money Classification"].value_counts()).reset_index()).iplot(kind="bar", x="index", y="Mobile Money Classification", title='Mobile Money Market')

### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Mobile Money Classification by Age

In [7]:
(px.histogram(data, data.age, color="Mobile Money Classification",nbins=20, opacity=0.60)).show()

### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Mobile Money Classification by Gender

In [8]:
male_with_mm = data[(data["gender"] == 1) & (data["mobile_money_classification"] != 10)]
female_with_mm = data[(data["gender"] == 2) & (data["mobile_money_classification"] != 10)]


fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=male_with_mm["Mobile Money Classification"].values, values= male_with_mm["mobile_money_classification"].values, title="Males with Money Mobile"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=female_with_mm["Mobile Money Classification"].values, values= female_with_mm["mobile_money_classification"].values, title="Females with Money Mobile"),
              row=1, col=2)



fig.update_layout(height=500, width= 800)

fig.show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Total Marital Status

In [9]:
data["Marital Status"].value_counts().iplot(kind='bar', title="Total Marital Status")

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Mobile Money Classification by Marital Status

In [10]:
married = data[data["Marital Status"] == "Married"]
single = data[data["Marital Status"] == "Single/Never Married"]
divorced = data[data["Marital Status"] == "Divorced"]
widowed = data[data["Marital Status"] == "Widowed"]

from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(
    rows=2, cols=2,
    specs=[[{"type": "domain"}, {"type": "domain"}],
           [{"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=married["Mobile Money Classification"].values, values= married["mobile_money_classification"].values, title="Married"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=single["Mobile Money Classification"].values, values= single["mobile_money_classification"].values, title="Single"),
              row=1, col=2)

fig.add_trace(go.Pie(labels=divorced["Mobile Money Classification"].values, values= divorced["mobile_money_classification"].values, title="Divorced"),
              row=2, col=1)

fig.add_trace(go.Pie(labels=widowed["Mobile Money Classification"].values, values= widowed["mobile_money_classification"].values, title="Widowed"),
              row=2, col=2)

fig.update_layout(height=700, width= 1000)

fig.show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Mobile Money Classification by Land Ownership

In [11]:
land =data[data["land_ownership"] == 1]
no_land = data[data["land_ownership"] == 2]

fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=land["Mobile Money Classification"].values, values= land["mobile_money_classification"].values, title="Land Owner"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=no_land["Mobile Money Classification"].values, values= no_land["mobile_money_classification"].values, title="No Land"),
              row=1, col=2)



fig.update_layout(height=500, width= 800)

fig.show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Type of Income of Mobile Money Users

In [12]:
income_data = data[data["mobile_money"] == 1]

types_of_income = income_data[['salaries_or_Wages','trading', 'services', 'piece_work', 'rental_income', 'interest',
       'pension', 'welfare', 'rely_on_someone', 'dependent', 'other']]

labels = []
values = []

for i in types_of_income:
    labels.append(i)
    values.append(sum(types_of_income[i]))
    
(go.Figure(data=[go.Pie(labels=labels, values= values)])).show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Mobile Money Classification by Type of Income

In [13]:
services = data[data["services"] == 1]
dependent = data[data["dependent"] == 1]
rental_income = data[data["rental_income"] == 1]
welfare = data[data["welfare"] == 1]


fig = make_subplots(
    rows=2, cols=2,
    specs=[[{"type": "domain"}, {"type": "domain"}],
           [{"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=services["Mobile Money Classification"].values, values= services["mobile_money_classification"].values, title="Income: Service"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=dependent["Mobile Money Classification"].values, values= dependent["mobile_money_classification"].values, title="Income: dependent"),
              row=1, col=2)

fig.add_trace(go.Pie(labels=rental_income["Mobile Money Classification"].values, values= rental_income["mobile_money_classification"].values, title="Income: Rental"),
              row=2, col=1)

fig.add_trace(go.Pie(labels=welfare["Mobile Money Classification"].values, values= welfare["mobile_money_classification"].values, title="Income: Welfare"),
              row=2, col=2)

fig.update_layout(height=700, width= 1000)

fig.show()

In [14]:
trading = data[data["trading"] == 1]
piece_work = data[data["piece_work"] == 1]
rely_on_someone = data[data["rely_on_someone"] == 1]
salaries_or_Wages = data[data["salaries_or_Wages"] == 1]
pension =  data[data["pension"] == 1]
interest = data[data["interest"] == 1]


fig = make_subplots(
    rows=2, cols=3,
    specs=[[{"type": "domain"}, {"type": "domain"}, {"type": "domain"}],
           [{"type": "domain"}, {"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=trading["Mobile Money Classification"].values, values= trading["mobile_money_classification"].values, title="Income: Trading"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=piece_work["Mobile Money Classification"].values, values= piece_work["mobile_money_classification"].values, title="Income: Piece Work"),
              row=1, col=2)

fig.add_trace(go.Pie(labels=pension["Mobile Money Classification"].values, values= pension["mobile_money_classification"].values, title="Income: Pension"),
              row=1, col=3)

fig.add_trace(go.Pie(labels=rely_on_someone["Mobile Money Classification"].values, values= rely_on_someone["mobile_money_classification"].values, title="Income: Rely On Someone"),
              row=2, col=1)

fig.add_trace(go.Pie(labels=salaries_or_Wages["Mobile Money Classification"].values, values= salaries_or_Wages["mobile_money_classification"].values, title="Income:Salaries or Wages"),
              row=2, col=2)

fig.add_trace(go.Pie(labels=salaries_or_Wages["Mobile Money Classification"].values, values= salaries_or_Wages["mobile_money_classification"].values, title="Income:Salaries or Wages"),
              row=2, col=3)

fig.update_layout(height=700, width= 1000)

fig.show()

**4. Create appropriate graphs to visually represent the relationship between how often mobile services are used and age, gender, marital status, land ownership and type of income.**

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Use of Mobile Money by Age (Buy Goods and Services)

In [15]:

(px.histogram(data, data.age, color="Usage Goods Service",nbins=20, opacity=0.60)).show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Use of Mobile Money by Age (Paying Bills)

In [16]:
(px.histogram(data, data.age, color="Usage Bills",nbins=20, opacity=0.60)).show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Use of Mobile Money by Gender: Buying Goods and Services

In [17]:
male =data[data["gender"] == 1]
female = data[data["gender"] == 2]

fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=male["Usage Goods Service"].values, values= male["usage_goods_services"].values, title="Males use of Mobile Money"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=female["Usage Goods Service"].values, values= female["usage_goods_services"].values, title="Female use of Mobile Money"),
              row=1, col=2)



fig.update_layout(height=500, width= 800)

fig.show()

#### &emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;&emsp;Use of Mobile Money by Gender: Paying Bills

In [18]:
male =data[data["gender"] == 1]
female = data[data["gender"] == 2]

fig = make_subplots(
    rows=1, cols=2,
    specs=[[{"type": "domain"}, {"type": "domain"}]],
)

fig.add_trace(go.Pie(labels=male["Usage Bills"].values, values= male["usage_bills"].values, title="Males use of Mobile Money: Paying Bills"),
              row=1, col=1)

fig.add_trace(go.Pie(labels=female["Usage Bills"].values, values= female["usage_bills"].values, title="Female use of Mobile Money: Paying Bills"),
              row=1, col=2)



fig.update_layout(height=500, width= 800)

fig.show()

**5. Create a map to visually explore geographic distribution of mobile services coverage with respect to type of income.**

In [19]:
trading_data = data[(data["mobile_money"] == 1) & (data["trading"] == 1) | (data["piece_work"] == 1)  | (data["salaries_or_Wages"] == 1) |(data["services"] == 1)  |(data["rental_income"] == 1) |(data["interest"] == 1) |(data["pension"] == 1)|(data["welfare"] == 1)|(data["rely_on_someone"] == 1)|(data["dependent"] == 1)|(data["other"] == 1)]
trading_map = folium.Map(location=[-6.161184, 35.745426], zoom_start=6)
marker_cluster = MarkerCluster().add_to(trading_map)
for lat, long in zip(trading_data.Latitude, trading_data.Longitude):
    folium.Marker(location = [lat, long]
    ).add_to(marker_cluster)

trading_map

**6. What can you conclude about use of financial services in Tanzania? Which demographic and geographic factors are associated with mobile money use?**

Market Segment

Out of the 7094 respondents:
3132 people use mobile money plus additional services
1778 people only use the services of mobile money but no have mobile mobile application
1386 people do not use mobile money at all, while the remaining 
804 have mobile money only without additional services

Age:

Most people that use mobile money only are between 20-24, while people within the 15 -19 are the one who do not have mobile mobile.
One can conclude that young adults are the one who uses mobile money

Gender:

77.4% of males use mobile money vs 69.7% of females use mobile money

Marital status:

Marital status does not seem to play any significant role in determining if a person will be a mobile money user or not. We see 74.5% people who are married use mobile money while
Single people are not far off with 74.4% and divorced sitting at 70.4 % and the minority being 
Widows only represented by 65.8%

